In [1]:
import pandas as pd
import numpy as np
import re

In [30]:
df = pd.read_csv("audible_uncleaned.csv")

In [31]:
df.head()

name                     author  \
0                  Geronimo Stilton #11 & #12  Writtenby:GeronimoStilton   
1                            The Burning Maze      Writtenby:RickRiordan   
2                                The Deep End       Writtenby:JeffKinney   
3                        Daughter of the Deep      Writtenby:RickRiordan   
4  The Lightning Thief: Percy Jackson, Book 1      Writtenby:RickRiordan   

                    narrator                time releasedate language  \
0      Narratedby:BillLobely   2 hrs and 20 mins    04-08-08  English   
1   Narratedby:RobbieDaymond   13 hrs and 8 mins    01-05-18  English   
2      Narratedby:DanRussell    2 hrs and 3 mins    06-11-20  English   
3  Narratedby:SoneelaNankani  11 hrs and 16 mins    05-10-21  English   
4  Narratedby:JesseBernstein              10 hrs    13-01-10  English   

                           stars   price  
0     5 out of 5 stars34 ratings  468.00  
1   4.5 out of 5 stars41 ratings  820.00  
2   4.5 out of 5 stars38 ratings  410.00  
3   4.5 out of 5 stars12 ratings  615.00  
4  4.5 out of 5 stars181 ratings  820.00

# 📚 Audiobook Metadata Dataset Summary
    This dataset contains metadata for a collection of audiobooks, primarily sourced from popular series and authors such as **Rick Riordan**, **Geronimo Stilton**, and **Jeff Kinney**. It is designed to provide insights into audiobook properties including duration, pricing, ratings, and publication details.
    

#### 🔢 Columns Overview:

| Column        | Description                                                                 |
|---------------|-----------------------------------------------------------------------------|
| `name`        | Title of the audiobook.                                                     |
| `author`      | Name of the book's author (prefixed with `Writtenby:`).                     |
| `narrator`    | Name of the audiobook's narrator (prefixed with `Narratedby:`).             |
| `time`        | Duration of the audiobook in hours and minutes.                             |
| `releasedate` | Release date of the audiobook (format: `YYYY-MM-DD`).                       |
| `language`    | Language of narration (mostly English).                                     |
| `stars`       | User ratings in the format: “X out of 5 stars Y ratings”.                   |
| `price`       | Price of the audiobook (likely in INR or other local currency).             |

#### 📊 Sample Insights:

- **Most frequent author:** Rick Riordan  
- **Typical duration:** Ranges from ~2 hrs to 13+ hrs  
- **Rating range:** 4.5 to 5 stars  
- **Price range:** 410 to 820 units  
- **Narrators:** Multiple unique narrators with varying popularity  


#### 🧹 Data Cleaning Notes:

- `author` and `narrator` fields contain prefixes (`Writtenby:`, `Narratedby:`) that may require stripping for analysis.  
- `stars` column contains mixed string data (rating + review count) which should be split.  
- `time` is in text format and can be converted to total minutes or seconds for quantitative analysis.

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 87489 entries, 0 to 87488
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   name         87489 non-null  object
 1   author       87489 non-null  object
 2   narrator     87489 non-null  object
 3   time         87489 non-null  object
 4   releasedate  87489 non-null  object
 5   language     87489 non-null  object
 6   stars        87489 non-null  object
 7   price        87489 non-null  object
dtypes: object(8)
memory usage: 5.3+ MB


### Problems In Dataset:
`Dirty Data`
- Column `name`
    - Line No. `(11,36,48,68,71,80, and 93)` there are some spelling mistakes `Accuracy`
    - There are have `Strange` name columns (eg. 87370, 87371 etc) `Validity`
- column `narrator` & `author`
    -  remove strange charecters. `Validity`
- column `releasedate`
    - There two types of releasedate
          1. `/`
          2. `-` `Consistency`
    - Dates are not in proper format `Accuracy`
- column `Price`
    - In this column there are sevaral values like `Free` we assume `Free == 0` `Completeness`
    - Chnageing Data Type `Validity`


`Messy Data`
- Column `author` & `narrator`
    - Remove `Writtenby:` & `Narratedby:`
    - Space between name and surname
    - `narrator` comma separate two names.
- Column `Stars`
    - 3 cols are in one data like `Given stars out of and ratings`
- Column `Time`
    - sparate `hrs` and `mins` and convert to mins.

# Automatic Assment
    * head and tail
    * sample 
    * info
    * is null 
    * duplicated 
    * describe

In [5]:
df.head()

name                     author  \
0                  Geronimo Stilton #11 & #12  Writtenby:GeronimoStilton   
1                            The Burning Maze      Writtenby:RickRiordan   
2                                The Deep End       Writtenby:JeffKinney   
3                        Daughter of the Deep      Writtenby:RickRiordan   
4  The Lightning Thief: Percy Jackson, Book 1      Writtenby:RickRiordan   

                    narrator                time releasedate language  \
0      Narratedby:BillLobely   2 hrs and 20 mins    04-08-08  English   
1   Narratedby:RobbieDaymond   13 hrs and 8 mins    01-05-18  English   
2      Narratedby:DanRussell    2 hrs and 3 mins    06-11-20  English   
3  Narratedby:SoneelaNankani  11 hrs and 16 mins    05-10-21  English   
4  Narratedby:JesseBernstein              10 hrs    13-01-10  English   

                           stars   price  
0     5 out of 5 stars34 ratings  468.00  
1   4.5 out of 5 stars41 ratings  820.00  
2   4.5 out of 5 stars38 ratings  410.00  
3   4.5 out of 5 stars12 ratings  615.00  
4  4.5 out of 5 stars181 ratings  820.00

In [9]:
df.sample(5)

name  \
47820                A los delincuentes hay que matarlos   
42958                                 Charity and Sylvia   
82281  A Primary Source History of the Colony of Sout...   
23313  Die Geschichte einer Bulimie und wie ich mich ...   
5175                                イッカボッグ [The Ickabog]   

                            author                  narrator  \
47820       Writtenby:RosaSilverio     Narratedby:MartaPérez   
42958   Writtenby:RachelHopeCleves  Narratedby:KristinKalbli   
82281       Writtenby:HeatherHasan  Narratedby:EileenStevens   
23313           Writtenby:InaVogel       Narratedby:InaVogel   
5175   Writtenby:J.K.ローリング,松岡佑子-翻訳          Narratedby:松嶋菜々子   

                     time releasedate  language          stars   price  
47820   3 hrs and 35 mins    14-03-22   spanish  Not rated yet  307.00  
42958  10 hrs and 55 mins    14-10-14   English  Not rated yet  836.00  
82281     1 hr and 2 mins    11-03-09   English  Not rated yet  266.00  
23313             25 mins    28-10-21    german  Not rated yet   99.00  
5175    9 hrs and 42 mins    24-11-20  japanese  Not rated yet  799.00

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 87489 entries, 0 to 87488
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   name         87489 non-null  object
 1   author       87489 non-null  object
 2   narrator     87489 non-null  object
 3   time         87489 non-null  object
 4   releasedate  87489 non-null  object
 5   language     87489 non-null  object
 6   stars        87489 non-null  object
 7   price        87489 non-null  object
dtypes: object(8)
memory usage: 5.3+ MB


In [13]:
df.isnull()

name  author  narrator   time  releasedate  language  stars  price
0      False   False     False  False        False     False  False  False
1      False   False     False  False        False     False  False  False
2      False   False     False  False        False     False  False  False
3      False   False     False  False        False     False  False  False
4      False   False     False  False        False     False  False  False
...      ...     ...       ...    ...          ...       ...    ...    ...
87484  False   False     False  False        False     False  False  False
87485  False   False     False  False        False     False  False  False
87486  False   False     False  False        False     False  False  False
87487  False   False     False  False        False     False  False  False
87488  False   False     False  False        False     False  False  False

[87489 rows x 8 columns]

In [15]:
df[df.duplicated()]

Empty DataFrame
Columns: [name, author, narrator, time, releasedate, language, stars, price]
Index: []

In [16]:
df.describe()

name              author              narrator    time  \
count            87489               87489                 87489   87489   
unique           82767               48374                 29717    2284   
top     The Art of War  Writtenby:矢島雅弘,石橋遊  Narratedby:anonymous  2 mins   
freq                20                 874                  1034     372   

       releasedate language          stars   price  
count        87489    87489          87489   87489  
unique        5058       36            665    1011  
top       16-05-18  English  Not rated yet  586.00  
freq           773    61884          72417    5533

# Order of severity
    Completeness <- Validity <- Accuracy <- Consistancy

# Data Cleaning Order
    1. Quality -> Completeness
    2. Tidiness
    3. Quality -> Validity
    4. Quality -> Acuuracy
    5. Quality -> Consistency

# Steps involved in Data Cleaning
    * Define
    * Code
    * Test
`Alaways make sure to create a copy of your pandas dataframe before you start the cleanimg process`

# Define
- Replace all `Free` values to `0` and change data type to float also remove coomas `,`.
    

In [32]:
df = df.copy()

In [33]:
df

name                     author  \
0                      Geronimo Stilton #11 & #12  Writtenby:GeronimoStilton   
1                                The Burning Maze      Writtenby:RickRiordan   
2                                    The Deep End       Writtenby:JeffKinney   
3                            Daughter of the Deep      Writtenby:RickRiordan   
4      The Lightning Thief: Percy Jackson, Book 1      Writtenby:RickRiordan   
...                                           ...                        ...   
87484                   Last Days of the Bus Club     Writtenby:ChrisStewart   
87485                                    The Alps    Writtenby:StephenO'Shea   
87486                        The Innocents Abroad        Writtenby:MarkTwain   
87487                       A Sentimental Journey   Writtenby:LaurenceSterne   
87488                                      Havana    Writtenby:MarkKurlansky   

                        narrator                time releasedate language  \
0          Narratedby:BillLobely   2 hrs and 20 mins    04-08-08  English   
1       Narratedby:RobbieDaymond   13 hrs and 8 mins    01-05-18  English   
2          Narratedby:DanRussell    2 hrs and 3 mins    06-11-20  English   
3      Narratedby:SoneelaNankani  11 hrs and 16 mins    05-10-21  English   
4      Narratedby:JesseBernstein              10 hrs    13-01-10  English   
...                          ...                 ...         ...      ...   
87484    Narratedby:ChrisStewart   7 hrs and 34 mins    09-03-17  English   
87485      Narratedby:RobertFass   10 hrs and 7 mins    21-02-17  English   
87486       Narratedby:FloGibson   19 hrs and 4 mins    30-12-16  English   
87487     Narratedby:AntonLesser    4 hrs and 8 mins    23-02-11  English   
87488     Narratedby:FleetCooper     6 hrs and 1 min    07-03-17  English   

                               stars   price  
0         5 out of 5 stars34 ratings  468.00  
1       4.5 out of 5 stars41 ratings  820.00  
2       4.5 out of 5 stars38 ratings  410.00  
3       4.5 out of 5 stars12 ratings  615.00  
4      4.5 out of 5 stars181 ratings  820.00  
...                              ...     ...  
87484                  Not rated yet  596.00  
87485                  Not rated yet  820.00  
87486                  Not rated yet  938.00  
87487                  Not rated yet  680.00  
87488                  Not rated yet  569.00  

[87489 rows x 8 columns]

In [34]:
df[df.price == 'Free']

name  \
983                             Ringo & the Yogi   
1414                        The Velveteen Rabbit   
1513       Billi Aur Moosarani [Cat and Musrani]   
2932           Pariyon Ki Kahaniya [Fairy Tales]   
4547         101 Best Indian Fables for Children   
...                                          ...   
80021                           FREE: The Undead   
81198                      Supporters. Le Pilote   
82644                         Boots Belts Berets   
86771                          Canada Is Awesome   
86927  Osez l'aventure avec Mike Horn. Le pilote   

                                     author  \
983                     Writtenby:PrasunRoy   
1414              Writtenby:MargeryWilliams   
1513                      Writtenby:Shivani   
2932                   Writtenby:JacobGrimm   
4547                   Writtenby:StutiGupta   
...                                     ...   
80021                   Writtenby:RRHaywood   
81198  Writtenby:PierreNiboyet,AudreyPoiret   
82644             Writtenby:TanushreePodder   
86771                Writtenby:NeilPasricha   
86927      Writtenby:MikeHorn,CharlesAudier   

                                narrator               time releasedate  \
983            Narratedby:SiddhantaPinto  5 hrs and 18 mins    19-11-19   
1414          Narratedby:RichardArmitage            24 mins    14-08-20   
1513              Narratedby:SarahHashmi            26 mins    14-10-21   
2932          Narratedby:AnuradhaChauhan  2 hrs and 15 mins    08-12-21   
4547      Narratedby:SunandhaRaghunathan  2 hrs and 26 mins    03-12-19   
...                                  ...                ...         ...   
80021               Narratedby:DanMorgan    1 hr and 3 mins    24-02-15   
81198          Narratedby:BorisRehlinger            24 mins    29-10-20   
82644    Narratedby:RannvijaySinghSingha  6 hrs and 59 mins    27-08-19   
86771            Narratedby:NeilPasricha            34 mins    09-10-18   
86927  Narratedby:MikeHorn,CharlesAudier            24 mins    11-01-22   

      language                          stars price  
983    English      4 out of 5 stars4 ratings  Free  
1414   English   4.5 out of 5 stars91 ratings  Free  
1513     Hindi                  Not rated yet  Free  
2932     Hindi                  Not rated yet  Free  
4547   English      4 out of 5 stars3 ratings  Free  
...        ...                            ...   ...  
80021  English      4 out of 5 stars8 ratings  Free  
81198   french                  Not rated yet  Free  
82644  English  4.5 out of 5 stars158 ratings  Free  
86771  English   4.5 out of 5 stars29 ratings  Free  
86927   french                  Not rated yet  Free  

[338 rows x 8 columns]

In [39]:
# code 
def convert(value):
    if value == 'Free':
        return 0
    else:
        return value
    

In [37]:
df['price'] = df.price.apply(convert)

In [38]:
df[df.price == 'Free']

Empty DataFrame
Columns: [name, author, narrator, time, releasedate, language, stars, price]
Index: []

In [45]:
df['price'] = df['price'].str.replace(',','')

In [48]:
df['price'] = df['price'].astype(float)

In [50]:
#Test
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 87489 entries, 0 to 87488
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   name         87489 non-null  object 
 1   author       87489 non-null  object 
 2   narrator     87489 non-null  object 
 3   time         87489 non-null  object 
 4   releasedate  87489 non-null  object 
 5   language     87489 non-null  object 
 6   stars        87489 non-null  object 
 7   price        87151 non-null  float64
dtypes: float64(1), object(7)
memory usage: 5.3+ MB


column `name`

# Define 
- Remove all `non ascai charecters` and `extra spaces`.

In [83]:
#code 
def remove_non_ascii(text):
    if pd.isna(text):
        return text
    # Remove all characters that are not in ASCII range
    return ''.join(char for char in text if ord(char) < 128)

In [54]:
df['name'] = df['name'].apply(remove_non_ascii)

In [55]:
df

name                     author  \
0                      Geronimo Stilton #11 & #12  Writtenby:GeronimoStilton   
1                                The Burning Maze      Writtenby:RickRiordan   
2                                    The Deep End       Writtenby:JeffKinney   
3                            Daughter of the Deep      Writtenby:RickRiordan   
4      The Lightning Thief: Percy Jackson, Book 1      Writtenby:RickRiordan   
...                                           ...                        ...   
87484                   Last Days of the Bus Club     Writtenby:ChrisStewart   
87485                                    The Alps    Writtenby:StephenO'Shea   
87486                        The Innocents Abroad        Writtenby:MarkTwain   
87487                       A Sentimental Journey   Writtenby:LaurenceSterne   
87488                                      Havana    Writtenby:MarkKurlansky   

                        narrator                time releasedate language  \
0          Narratedby:BillLobely   2 hrs and 20 mins    04-08-08  English   
1       Narratedby:RobbieDaymond   13 hrs and 8 mins    01-05-18  English   
2          Narratedby:DanRussell    2 hrs and 3 mins    06-11-20  English   
3      Narratedby:SoneelaNankani  11 hrs and 16 mins    05-10-21  English   
4      Narratedby:JesseBernstein              10 hrs    13-01-10  English   
...                          ...                 ...         ...      ...   
87484    Narratedby:ChrisStewart   7 hrs and 34 mins    09-03-17  English   
87485      Narratedby:RobertFass   10 hrs and 7 mins    21-02-17  English   
87486       Narratedby:FloGibson   19 hrs and 4 mins    30-12-16  English   
87487     Narratedby:AntonLesser    4 hrs and 8 mins    23-02-11  English   
87488     Narratedby:FleetCooper     6 hrs and 1 min    07-03-17  English   

                               stars  price  
0         5 out of 5 stars34 ratings  468.0  
1       4.5 out of 5 stars41 ratings  820.0  
2       4.5 out of 5 stars38 ratings  410.0  
3       4.5 out of 5 stars12 ratings  615.0  
4      4.5 out of 5 stars181 ratings  820.0  
...                              ...    ...  
87484                  Not rated yet  596.0  
87485                  Not rated yet  820.0  
87486                  Not rated yet  938.0  
87487                  Not rated yet  680.0  
87488                  Not rated yet  569.0  

[87489 rows x 8 columns]

In [56]:
def clean_text(text):
    if pd.isna(text):
        return None
    text = text.strip()
    if re.fullmatch(r'[\W\d\s_]+',text):
        return None
    if len(text) < 3:
        return None
    return text

In [59]:
df['name'] = df['name'].apply(clean_text)

In [62]:
df[df.name == None]

Empty DataFrame
Columns: [name, author, narrator, time, releasedate, language, stars, price]
Index: []

In [78]:
def clean_name(text):
    if pd.isna(text):
        return text
    text = re.sub(r'\[|\]', '', text)
    text = re.sub(r'^\s*-\s*', '', text)

    # Normalize multiple spaces to single
    text = re.sub(r'\s+', ' ', text)
    return text.strip()

In [81]:
df['name'] = df['name'].apply(clean_name)

In [82]:
df

name                     author  \
0                      Geronimo Stilton #11 & #12  Writtenby:GeronimoStilton   
1                                The Burning Maze      Writtenby:RickRiordan   
2                                    The Deep End       Writtenby:JeffKinney   
3                            Daughter of the Deep      Writtenby:RickRiordan   
4      The Lightning Thief: Percy Jackson, Book 1      Writtenby:RickRiordan   
...                                           ...                        ...   
87484                   Last Days of the Bus Club     Writtenby:ChrisStewart   
87485                                    The Alps    Writtenby:StephenO'Shea   
87486                        The Innocents Abroad        Writtenby:MarkTwain   
87487                       A Sentimental Journey   Writtenby:LaurenceSterne   
87488                                      Havana    Writtenby:MarkKurlansky   

                        narrator                time releasedate language  \
0          Narratedby:BillLobely   2 hrs and 20 mins    04-08-08  English   
1       Narratedby:RobbieDaymond   13 hrs and 8 mins    01-05-18  English   
2          Narratedby:DanRussell    2 hrs and 3 mins    06-11-20  English   
3      Narratedby:SoneelaNankani  11 hrs and 16 mins    05-10-21  English   
4      Narratedby:JesseBernstein              10 hrs    13-01-10  English   
...                          ...                 ...         ...      ...   
87484    Narratedby:ChrisStewart   7 hrs and 34 mins    09-03-17  English   
87485      Narratedby:RobertFass   10 hrs and 7 mins    21-02-17  English   
87486       Narratedby:FloGibson   19 hrs and 4 mins    30-12-16  English   
87487     Narratedby:AntonLesser    4 hrs and 8 mins    23-02-11  English   
87488     Narratedby:FleetCooper     6 hrs and 1 min    07-03-17  English   

                               stars  price  
0         5 out of 5 stars34 ratings  468.0  
1       4.5 out of 5 stars41 ratings  820.0  
2       4.5 out of 5 stars38 ratings  410.0  
3       4.5 out of 5 stars12 ratings  615.0  
4      4.5 out of 5 stars181 ratings  820.0  
...                              ...    ...  
87484                  Not rated yet  596.0  
87485                  Not rated yet  820.0  
87486                  Not rated yet  938.0  
87487                  Not rated yet  680.0  
87488                  Not rated yet  569.0  

[87489 rows x 8 columns]

In [86]:
#Test
def is_garbled(text):
    if pd.isna(text):
        return False
    # Detect if text has many non-ASCII chars
    return bool(re.search(r'[^\x00-\x7F]{3,}', text))

In [87]:
df[df['name'].apply(is_garbled)]['name']

Series([], Name: name, dtype: object)

column `narrator` and `author`

# Define
- In this case we remove in author column `Writtenby` and in narrator column `Narratedby` and giving space between narrator name and surname and also have some isuue their have some speacial charecter between names remove those and separate comma separated names.

In [ ]:
df.head()

**code**

In [93]:
df['author'] = df['author'].str.replace('Writtenby:','')

In [94]:
df['narrator'] = df['narrator'].str.replace('Narratedby:','')

In [95]:
df

name           author  \
0                      Geronimo Stilton #11 & #12  GeronimoStilton   
1                                The Burning Maze      RickRiordan   
2                                    The Deep End       JeffKinney   
3                            Daughter of the Deep      RickRiordan   
4      The Lightning Thief: Percy Jackson, Book 1      RickRiordan   
...                                           ...              ...   
87484                   Last Days of the Bus Club     ChrisStewart   
87485                                    The Alps    StephenO'Shea   
87486                        The Innocents Abroad        MarkTwain   
87487                       A Sentimental Journey   LaurenceSterne   
87488                                      Havana    MarkKurlansky   

             narrator                time releasedate language  \
0          BillLobely   2 hrs and 20 mins    04-08-08  English   
1       RobbieDaymond   13 hrs and 8 mins    01-05-18  English   
2          DanRussell    2 hrs and 3 mins    06-11-20  English   
3      SoneelaNankani  11 hrs and 16 mins    05-10-21  English   
4      JesseBernstein              10 hrs    13-01-10  English   
...               ...                 ...         ...      ...   
87484    ChrisStewart   7 hrs and 34 mins    09-03-17  English   
87485      RobertFass   10 hrs and 7 mins    21-02-17  English   
87486       FloGibson   19 hrs and 4 mins    30-12-16  English   
87487     AntonLesser    4 hrs and 8 mins    23-02-11  English   
87488     FleetCooper     6 hrs and 1 min    07-03-17  English   

                               stars  price  
0         5 out of 5 stars34 ratings  468.0  
1       4.5 out of 5 stars41 ratings  820.0  
2       4.5 out of 5 stars38 ratings  410.0  
3       4.5 out of 5 stars12 ratings  615.0  
4      4.5 out of 5 stars181 ratings  820.0  
...                              ...    ...  
87484                  Not rated yet  596.0  
87485                  Not rated yet  820.0  
87486                  Not rated yet  938.0  
87487                  Not rated yet  680.0  
87488                  Not rated yet  569.0  

[87489 rows x 8 columns]

In [96]:
def format_names(text):
    if pd.isna(text):
        return text
    text = re.sub(r'[^a-zA-Z,\s]', '', text)

    names = text.split(',')

    result = []
    for name in names:
        name = name.strip()
        spaced = ' '.join(re.findall(r'[A-Z][a-z]*', name))
        if spaced:
            result.append(spaced)

    return ', '.join(result)
    

In [99]:
df['author'] = df['author'].apply(format_names)

In [100]:
df['narrator'] = df['narrator'].apply(format_names)

In [101]:
df

name            author  \
0                      Geronimo Stilton #11 & #12  Geronimo Stilton   
1                                The Burning Maze      Rick Riordan   
2                                    The Deep End       Jeff Kinney   
3                            Daughter of the Deep      Rick Riordan   
4      The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   
...                                           ...               ...   
87484                   Last Days of the Bus Club     Chris Stewart   
87485                                    The Alps    Stephen O Shea   
87486                        The Innocents Abroad        Mark Twain   
87487                       A Sentimental Journey   Laurence Sterne   
87488                                      Havana    Mark Kurlansky   

              narrator                time releasedate language  \
0          Bill Lobely   2 hrs and 20 mins    04-08-08  English   
1       Robbie Daymond   13 hrs and 8 mins    01-05-18  English   
2          Dan Russell    2 hrs and 3 mins    06-11-20  English   
3      Soneela Nankani  11 hrs and 16 mins    05-10-21  English   
4      Jesse Bernstein              10 hrs    13-01-10  English   
...                ...                 ...         ...      ...   
87484    Chris Stewart   7 hrs and 34 mins    09-03-17  English   
87485      Robert Fass   10 hrs and 7 mins    21-02-17  English   
87486       Flo Gibson   19 hrs and 4 mins    30-12-16  English   
87487     Anton Lesser    4 hrs and 8 mins    23-02-11  English   
87488     Fleet Cooper     6 hrs and 1 min    07-03-17  English   

                               stars  price  
0         5 out of 5 stars34 ratings  468.0  
1       4.5 out of 5 stars41 ratings  820.0  
2       4.5 out of 5 stars38 ratings  410.0  
3       4.5 out of 5 stars12 ratings  615.0  
4      4.5 out of 5 stars181 ratings  820.0  
...                              ...    ...  
87484                  Not rated yet  596.0  
87485                  Not rated yet  820.0  
87486                  Not rated yet  938.0  
87487                  Not rated yet  680.0  
87488                  Not rated yet  569.0  

[87489 rows x 8 columns]

In [102]:
df.to_csv('last_change.csv',index=False)

In [3]:
df = pd.read_csv('last_change.csv')

# DEFINE
- clean `time` column extract and differentiate hours and mintues from the column and also make a new column called `Seconds`

In [4]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate language  \
0      Bill Lobely   2 hrs and 20 mins    04-08-08  English   
1   Robbie Daymond   13 hrs and 8 mins    01-05-18  English   
2      Dan Russell    2 hrs and 3 mins    06-11-20  English   
3  Soneela Nankani  11 hrs and 16 mins    05-10-21  English   
4  Jesse Bernstein              10 hrs    13-01-10  English   

                           stars  price  
0     5 out of 5 stars34 ratings  468.0  
1   4.5 out of 5 stars41 ratings  820.0  
2   4.5 out of 5 stars38 ratings  410.0  
3   4.5 out of 5 stars12 ratings  615.0  
4  4.5 out of 5 stars181 ratings  820.0

In [5]:
import pandas as pd

# Show full column values without truncation
pd.set_option('display.max_colwidth', None)

# Show all rows if needed
pd.set_option('display.max_rows', None)

# Show all columns if you have many columns
pd.set_option('display.max_columns', None)


In [6]:
def hr_min_extractor(time_list):
    hrs = 0
    mins = 0
    
    if 'hr' in time_list or 'hrs' in time_list:
        hrs = int(time_list[0])
    
    if 'min' in time_list or 'mins' in time_list:
        # If only minutes present
        if time_list[1] in ['min', 'mins']:
            mins = int(time_list[0])
        else:
            mins = int(time_list[-2])
    
    return hrs, mins


In [7]:
df['time_split'] = df['time'].str.split(' ')
df[['hours', 'minutes']] = df['time_split'].apply(lambda x: pd.Series(hr_min_extractor(x)))


In [8]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate language  \
0      Bill Lobely   2 hrs and 20 mins    04-08-08  English   
1   Robbie Daymond   13 hrs and 8 mins    01-05-18  English   
2      Dan Russell    2 hrs and 3 mins    06-11-20  English   
3  Soneela Nankani  11 hrs and 16 mins    05-10-21  English   
4  Jesse Bernstein              10 hrs    13-01-10  English   

                           stars  price                time_split  hours  \
0     5 out of 5 stars34 ratings  468.0   [2, hrs, and, 20, mins]      2   
1   4.5 out of 5 stars41 ratings  820.0   [13, hrs, and, 8, mins]     13   
2   4.5 out of 5 stars38 ratings  410.0    [2, hrs, and, 3, mins]      2   
3   4.5 out of 5 stars12 ratings  615.0  [11, hrs, and, 16, mins]     11   
4  4.5 out of 5 stars181 ratings  820.0                 [10, hrs]     10   

   minutes  
0       20  
1        8  
2        3  
3       16  
4        0

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 87489 entries, 0 to 87488
Data columns (total 11 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   name         83633 non-null  object 
 1   author       83731 non-null  object 
 2   narrator     81950 non-null  object 
 3   time         87489 non-null  object 
 4   releasedate  87489 non-null  object 
 5   language     87489 non-null  object 
 6   stars        87489 non-null  object 
 7   price        87151 non-null  float64
 8   time_split   87489 non-null  object 
 9   hours        87489 non-null  int64  
 10  minutes      87489 non-null  int64  
dtypes: float64(1), int64(2), object(8)
memory usage: 7.3+ MB


In [10]:
df['Seconds'] = df['hours']*3600 + df['minutes']*60

In [11]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate language  \
0      Bill Lobely   2 hrs and 20 mins    04-08-08  English   
1   Robbie Daymond   13 hrs and 8 mins    01-05-18  English   
2      Dan Russell    2 hrs and 3 mins    06-11-20  English   
3  Soneela Nankani  11 hrs and 16 mins    05-10-21  English   
4  Jesse Bernstein              10 hrs    13-01-10  English   

                           stars  price                time_split  hours  \
0     5 out of 5 stars34 ratings  468.0   [2, hrs, and, 20, mins]      2   
1   4.5 out of 5 stars41 ratings  820.0   [13, hrs, and, 8, mins]     13   
2   4.5 out of 5 stars38 ratings  410.0    [2, hrs, and, 3, mins]      2   
3   4.5 out of 5 stars12 ratings  615.0  [11, hrs, and, 16, mins]     11   
4  4.5 out of 5 stars181 ratings  820.0                 [10, hrs]     10   

   minutes  Seconds  
0       20     8400  
1        8    47280  
2        3     7380  
3       16    40560  
4        0    36000

# DEFINE
- Clean the `stars` column and make  columns from this column `Avarage_Rating(out of 5)`(It gives avarage ratings of the movie), `Person_Rated`(It gives how many person rated)

In [29]:
def star_extractor(column):
    if 'Not' in column:
        return column
    else:
        return [column[0],column[3],column[4]]
    

In [21]:
df['stars'].isna().sum()

0

In [32]:
avg_rating = df['stars'].str.split(' ').apply(star_extractor).str.get(0)

In [38]:
person_rated = df['stars'].str.split(' ').apply(star_extractor).str.get(2).str.findall('stars\s*(\d+)').str.get(0).astype(float)

<>:1: SyntaxWarning: invalid escape sequence '\s'
<>:1: SyntaxWarning: invalid escape sequence '\s'
C:\Users\Dell\AppData\Local\Temp\ipykernel_13628\3509230065.py:1: SyntaxWarning: invalid escape sequence '\s'
  person_rated = df['stars'].str.split(' ').apply(star_extractor).str.get(2).str.findall('stars\s*(\d+)').str.get(0).astype(float)


In [52]:
def define(cols):
    if cols == 'Not':
        return np.nan
    else:
        return cols
        

In [59]:
avg_rating = avg_rating.apply(define).astype(float)

In [56]:
person_rated.isna().sum()

72417

In [60]:
df.insert(7,'Avarage_Rating(out of 5)',avg_rating)
df.insert(8,'Person_Rated',person_rated)

In [61]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate language  \
0      Bill Lobely   2 hrs and 20 mins    04-08-08  English   
1   Robbie Daymond   13 hrs and 8 mins    01-05-18  English   
2      Dan Russell    2 hrs and 3 mins    06-11-20  English   
3  Soneela Nankani  11 hrs and 16 mins    05-10-21  English   
4  Jesse Bernstein              10 hrs    13-01-10  English   

                           stars  Avarage_Rating(out of 5)  Person_Rated  \
0     5 out of 5 stars34 ratings                       5.0          34.0   
1   4.5 out of 5 stars41 ratings                       4.5          41.0   
2   4.5 out of 5 stars38 ratings                       4.5          38.0   
3   4.5 out of 5 stars12 ratings                       4.5          12.0   
4  4.5 out of 5 stars181 ratings                       4.5         181.0   

   price                time_split  hours  minutes  Seconds  
0  468.0   [2, hrs, and, 20, mins]      2       20     8400  
1  820.0   [13, hrs, and, 8, mins]     13        8    47280  
2  410.0    [2, hrs, and, 3, mins]      2        3     7380  
3  615.0  [11, hrs, and, 16, mins]     11       16    40560  
4  820.0                 [10, hrs]     10        0    36000

# DEFINE
- convert `releasedate` column proper dattime format and make one columns extra `Release Month`.

In [64]:
df['releasedate'] = pd.to_datetime(df['releasedate'])

C:\Users\Dell\AppData\Local\Temp\ipykernel_13628\1614981251.py:1: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['releasedate'] = pd.to_datetime(df['releasedate'])


In [66]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate language  \
0      Bill Lobely   2 hrs and 20 mins  2008-04-08  English   
1   Robbie Daymond   13 hrs and 8 mins  2018-01-05  English   
2      Dan Russell    2 hrs and 3 mins  2020-06-11  English   
3  Soneela Nankani  11 hrs and 16 mins  2021-05-10  English   
4  Jesse Bernstein              10 hrs  2010-01-13  English   

                           stars  Avarage_Rating(out of 5)  Person_Rated  \
0     5 out of 5 stars34 ratings                       5.0          34.0   
1   4.5 out of 5 stars41 ratings                       4.5          41.0   
2   4.5 out of 5 stars38 ratings                       4.5          38.0   
3   4.5 out of 5 stars12 ratings                       4.5          12.0   
4  4.5 out of 5 stars181 ratings                       4.5         181.0   

   price                time_split  hours  minutes  Seconds  
0  468.0   [2, hrs, and, 20, mins]      2       20     8400  
1  820.0   [13, hrs, and, 8, mins]     13        8    47280  
2  410.0    [2, hrs, and, 3, mins]      2        3     7380  
3  615.0  [11, hrs, and, 16, mins]     11       16    40560  
4  820.0                 [10, hrs]     10        0    36000

In [69]:
month_name = df['releasedate'].dt.month_name()

In [70]:
df.insert(5,'Release Month',month_name)

In [71]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate Release Month language  \
0      Bill Lobely   2 hrs and 20 mins  2008-04-08         April  English   
1   Robbie Daymond   13 hrs and 8 mins  2018-01-05       January  English   
2      Dan Russell    2 hrs and 3 mins  2020-06-11          June  English   
3  Soneela Nankani  11 hrs and 16 mins  2021-05-10           May  English   
4  Jesse Bernstein              10 hrs  2010-01-13       January  English   

                           stars  Avarage_Rating(out of 5)  Person_Rated  \
0     5 out of 5 stars34 ratings                       5.0          34.0   
1   4.5 out of 5 stars41 ratings                       4.5          41.0   
2   4.5 out of 5 stars38 ratings                       4.5          38.0   
3   4.5 out of 5 stars12 ratings                       4.5          12.0   
4  4.5 out of 5 stars181 ratings                       4.5         181.0   

   price                time_split  hours  minutes  Seconds  
0  468.0   [2, hrs, and, 20, mins]      2       20     8400  
1  820.0   [13, hrs, and, 8, mins]     13        8    47280  
2  410.0    [2, hrs, and, 3, mins]      2        3     7380  
3  615.0  [11, hrs, and, 16, mins]     11       16    40560  
4  820.0                 [10, hrs]     10        0    36000

In [74]:
day_name = df['releasedate'].dt.day_name()

In [75]:
df.insert(6,'Release Day',day_name)

In [76]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate Release Month Release Day  \
0      Bill Lobely   2 hrs and 20 mins  2008-04-08         April     Tuesday   
1   Robbie Daymond   13 hrs and 8 mins  2018-01-05       January      Friday   
2      Dan Russell    2 hrs and 3 mins  2020-06-11          June    Thursday   
3  Soneela Nankani  11 hrs and 16 mins  2021-05-10           May      Monday   
4  Jesse Bernstein              10 hrs  2010-01-13       January   Wednesday   

  language                          stars  Avarage_Rating(out of 5)  \
0  English     5 out of 5 stars34 ratings                       5.0   
1  English   4.5 out of 5 stars41 ratings                       4.5   
2  English   4.5 out of 5 stars38 ratings                       4.5   
3  English   4.5 out of 5 stars12 ratings                       4.5   
4  English  4.5 out of 5 stars181 ratings                       4.5   

   Person_Rated  price                time_split  hours  minutes  Seconds  
0          34.0  468.0   [2, hrs, and, 20, mins]      2       20     8400  
1          41.0  820.0   [13, hrs, and, 8, mins]     13        8    47280  
2          38.0  410.0    [2, hrs, and, 3, mins]      2        3     7380  
3          12.0  615.0  [11, hrs, and, 16, mins]     11       16    40560  
4         181.0  820.0                 [10, hrs]     10        0    36000

In [81]:
df['language'] = df['language'].str.lower()

In [82]:
df.head()

name            author  \
0                  Geronimo Stilton #11 & #12  Geronimo Stilton   
1                            The Burning Maze      Rick Riordan   
2                                The Deep End       Jeff Kinney   
3                        Daughter of the Deep      Rick Riordan   
4  The Lightning Thief: Percy Jackson, Book 1      Rick Riordan   

          narrator                time releasedate Release Month Release Day  \
0      Bill Lobely   2 hrs and 20 mins  2008-04-08         April     Tuesday   
1   Robbie Daymond   13 hrs and 8 mins  2018-01-05       January      Friday   
2      Dan Russell    2 hrs and 3 mins  2020-06-11          June    Thursday   
3  Soneela Nankani  11 hrs and 16 mins  2021-05-10           May      Monday   
4  Jesse Bernstein              10 hrs  2010-01-13       January   Wednesday   

  language                          stars  Avarage_Rating(out of 5)  \
0  english     5 out of 5 stars34 ratings                       5.0   
1  english   4.5 out of 5 stars41 ratings                       4.5   
2  english   4.5 out of 5 stars38 ratings                       4.5   
3  english   4.5 out of 5 stars12 ratings                       4.5   
4  english  4.5 out of 5 stars181 ratings                       4.5   

   Person_Rated  price                time_split  hours  minutes  Seconds  
0          34.0  468.0   [2, hrs, and, 20, mins]      2       20     8400  
1          41.0  820.0   [13, hrs, and, 8, mins]     13        8    47280  
2          38.0  410.0    [2, hrs, and, 3, mins]      2        3     7380  
3          12.0  615.0  [11, hrs, and, 16, mins]     11       16    40560  
4         181.0  820.0                 [10, hrs]     10        0    36000

In [83]:
df['author'].value_counts()

author
Smart Reading                                                                                                   405
B J                                                                                                             311
Online Studio Productions                                                                                       212
William Shakespeare                                                                                             201
Bill Brown                                                                                                      198
J M Gardner                                                                                                     174
Innovative Language Learning                                                                                    167
Gertrude Chandler Warner                                                                                        160
Minds                                                            

In [84]:
df.to_csv('almost_done.csv',index=False)

In [88]:
df['Avarage_Rating(out of 5)'] = df['Avarage_Rating(out of 5)'].fillna(0)

In [90]:
df['Person_Rated'] = df['Person_Rated'].fillna(0)

In [91]:
df.isna().sum()

name                        3856
author                      3758
narrator                    5539
time                           0
releasedate                    0
Release Month                  0
Release Day                    0
language                       0
stars                          0
Avarage_Rating(out of 5)       0
Person_Rated                   0
price                        338
time_split                     0
hours                          0
minutes                        0
Seconds                        0
dtype: int64

In [92]:
df.to_csv('almost_done.csv',index=False)

In [2]:
df = pd.read_csv('almost_done.csv')

In [3]:
df.to_excel('almost_done.xlsx')

In [5]:
df.isnull().sum()

name                        3856
author                      3758
narrator                    5539
time                           0
releasedate                    0
Release Month                  0
Release Day                    0
language                       0
stars                          0
Avarage_Rating(out of 5)       0
Person_Rated                   0
price                        338
time_split                     0
hours                          0
minutes                        0
Seconds                        0
dtype: int64

In [6]:
df.head(1)

name            author     narrator  \
0  Geronimo Stilton #11 & #12  Geronimo Stilton  Bill Lobely   

                time releasedate Release Month Release Day language  \
0  2 hrs and 20 mins  2008-04-08         April     Tuesday  english   

                        stars  Avarage_Rating(out of 5)  Person_Rated  price  \
0  5 out of 5 stars34 ratings                       5.0          34.0  468.0   

                          time_split  hours  minutes  Seconds  
0  ['2', 'hrs', 'and', '20', 'mins']      2       20     8400

In [12]:
df.shape

(87489, 16)

In [15]:
df = df.dropna(subset=['name','author','narrator'],how='all')

In [16]:
df.to_excel('almost_done.xlsx')

In [17]:
df.isna().sum()

name                         905
author                       807
narrator                    2588
time                           0
releasedate                    0
Release Month                  0
Release Day                    0
language                       0
stars                          0
Avarage_Rating(out of 5)       0
Person_Rated                   0
price                        338
time_split                     0
hours                          0
minutes                        0
Seconds                        0
dtype: int64